In [3]:

import pandas as pd
pd.options.mode.chained_assignment = None
pd.set_option('display.max_columns', None)

import altair as alt
# from altair_saver import save

from ast import literal_eval

import warnings
warnings.filterwarnings("ignore")

import sys
sys.path.append("..")
from network_analysis.load_datasets import get_updated_shxco_data



In [4]:
members_df, books_df, borrow_events, events_df = get_updated_shxco_data(
    get_subscription=False)


In [3]:
def split_cols(original_df):
    df = original_df[original_df.exceptional_types.isna() == False]
    df.exceptional_types = df.exceptional_types.apply(literal_eval)
    if 'exceptional_counts' in df.columns:
        df.exceptional_counts = df.exceptional_counts.apply(literal_eval)
        df = df.explode(['exceptional_types', 'exceptional_counts'])
    else:
        df = df.explode(['exceptional_types'])
    return df

In [4]:
ex_books_df = split_cols(books_df)
grouped_books = ex_books_df.groupby(
    'exceptional_types').size().reset_index(name='counts')
grouped_books['type'] = 'books'

ex_members_df = split_cols(members_df)
grouped_members = ex_members_df.groupby(
    'exceptional_types').size().reset_index(name='counts')
grouped_members['type'] = 'members'

ex_events_df = split_cols(events_df)
grouped_events = ex_events_df.groupby(
    'exceptional_types').size().reset_index(name='counts')
grouped_events['type'] = 'events'


In [5]:
def update_values(df):
    df.loc[df['exceptional_types'] ==
               'sunday_shopers', 'exceptional_types'] = 'Sunday Shoppers'
    df.loc[df['exceptional_types'] ==
                'longterm_borrows', 'exceptional_types'] = 'Longterm Borrows'
    df.loc[df['exceptional_types'] == 'overborrows',
                'exceptional_types'] = 'Borrows Beyond Subscription'

    df.loc[df['exceptional_types'] ==
                'post1942_events', 'exceptional_types'] = 'Borrows After 1942'

    df.loc[df['exceptional_types'] ==
                'unknown_borrows', 'exceptional_types'] = 'Borrow Status Unknown'

    df.loc[df['exceptional_types'] ==
                'missing_events', 'exceptional_types'] = 'Borrow Status Missing'
    return df


In [6]:
def get_correlation_df(original_df, col):
    df = split_cols(original_df)
    df.exceptional_counts = df.exceptional_counts.astype(int)
    df = update_values(df)
    grouped_df = df.groupby([col, 'exceptional_types'])['exceptional_counts'].sum().reset_index()
    pivoted_df = grouped_df.pivot(index=col, columns='exceptional_types', values='exceptional_counts').reset_index()
    pivoted_df.fillna(0, inplace=True)
    pivot_cols = grouped_df.exceptional_types.unique().tolist()
    corr_df = pivoted_df[pivot_cols].corr().reset_index()
    corr_df['cat'] = corr_df.exceptional_types
    return corr_df, pivot_cols

def get_correlation_chart(original_df, col, title):
    corr_df, pivot_cols = get_correlation_df(original_df, col)
    base = alt.Chart(corr_df).transform_fold(pivot_cols).encode(
        x=alt.X("cat:N", axis=alt.Axis(title='', labelAngle=-45)),  
        y=alt.Y('key:N', axis=alt.Axis(title=''))
    ).properties(height=300, width=300, title=title)
    boxes = base.mark_rect().encode(color=alt.Color(
        "value:Q", scale=alt.Scale(scheme="redyellowblue")))
    labels = base.mark_text(size=5, color="grey").encode(
        text=alt.Text("value:Q", format="0.1f"))
    chart = boxes + labels
    return chart

In [7]:
members_corr, pivot_cols = get_correlation_df(members_df, 'member_id')
books_corr, pivot_cols = get_correlation_df(books_df, 'id')

In [12]:
members_type = "Correlations in Members' Borrowing Activity Beyond Guidelines"
books_type = "Correlations in Books Being Borrowed Beyond Guidelines"
members_corr['type'] = members_type
books_corr["type"] = books_type

In [13]:
corr_concat = pd.concat([members_corr, books_corr])
corr_concat[0:1]

exceptional_types   exceptional_types  Borrows After 1942  \
0                  Borrows After 1942                 1.0   

exceptional_types  Borrows Beyond Subscription  Sunday Shoppers  \
0                                     0.116059         0.363714   

exceptional_types  Borrow Status Unknown  Borrow Status Missing  \
0                               0.327669              -0.015114   

exceptional_types  Longterm Borrows                 cat  \
0                         -0.002875  Borrows After 1942   

exceptional_types                                               type  
0                  Correlations in Members' Borrowing Activity Be...

In [14]:
base = alt.Chart(corr_concat).transform_fold(pivot_cols).encode(
    x=alt.X("cat:N", axis=alt.Axis(title='', labelAngle=-45)),  
    y=alt.Y('key:N', axis=alt.Axis(title=''))
    ).properties(height=300, width=300)
boxes = base.mark_rect().encode(color=alt.Color(
    "value:Q", scale=alt.Scale(scheme="redyellowblue")))
labels = base.mark_text(size=5, color="grey").encode(
    text=alt.Text("value:Q", format="0.1f"))
chart = boxes + labels
chart.facet(
    row=alt.Row('type:N', header=alt.Header(labelOrient='top'), sort=[members_type,books_type])
    )

alt.FacetChart(...)

In [104]:
chart_books = get_correlation_df(books_df, 'id', 'Correlations in Exceptional Books')
chart_members = get_correlation_df(members_df, 'member_id', 'Correlations in Exceptional Members')

alt.vconcat(*[chart_members, chart_books])

alt.VConcatChart(...)

In [105]:
grouped_df = pd.concat([grouped_books, grouped_members, grouped_events])
grouped_df = update_values(grouped_df)


In [106]:
grouped_df

exceptional_types  counts     type
0             Longterm Borrows      23    books
1        Borrow Status Missing       4    books
2  Borrows Beyond Subscription    2931    books
3           Borrows After 1942     392    books
4              Sunday Shoppers     246    books
5        Borrow Status Unknown     539    books
0             Longterm Borrows      12  members
1        Borrow Status Missing       4  members
2  Borrows Beyond Subscription     277  members
3           Borrows After 1942     119  members
4              Sunday Shoppers     101  members
5        Borrow Status Unknown     219  members
0             Longterm Borrows      24   events
1        Borrow Status Missing       4   events
2  Borrows Beyond Subscription    5752   events
3           Borrows After 1942     538   events
4              Sunday Shoppers     258   events
5        Borrow Status Unknown     604   events

In [107]:

chart = alt.Chart(grouped_df).mark_bar().encode(
    y=alt.Y('type:O', sort=alt.EncodingSortField(
        field='counts', op='sum', order='descending'), title=''),
    x=alt.X('counts:Q', title=''),
    color=alt.Color('type:N', legend=alt.Legend(title='Library Dataset'), sort=alt.EncodingSortField(field='counts', op='sum', order='descending')),
).properties(
    width=100,
    height=100,
).facet(
    facet=alt.Facet('exceptional_types:O', title=None),
    columns=3,
    title='Rate of Exceptional Behavior in the Library (Scale Independent)'
).resolve_scale(x='independent')
chart
# chart.save('./visualizations/exceptional_metadata.png', scale_factor=2.0)


alt.FacetChart(...)

In [8]:
test = pd.read_csv('../dataset_generator/source_data/SCoData_events_v1.1_2021-01.csv')
test.event_type.value_counts()

Borrow                     21061
Renewal                     4811
Subscription                4717
Reimbursement               2759
Purchase                     812
Crossed out                  284
Generic                      244
Supplement                   231
Separate Deposit              33
Request                       29
Gift                          25
Periodical Subscription       14
Loan                          11
Name: event_type, dtype: int64

In [10]:
test = pd.read_csv('../dataset_generator/source_data/SCoData_events_v1.2_2022-01.csv')
test.event_type.unique()

array(['Generic', 'Subscription', 'Borrow', 'Crossed out', 'Purchase',
       'Renewal', 'Reimbursement', 'Gift', 'Request', 'Supplement',
       'Separate Payment', 'Periodical Subscription'], dtype=object)

In [12]:
event_types = ['Subscription', 'Renewal', 'Reimbursement', 'Supplement',
       'Separate Payment']
test = test[test.event_type.isin(event_types)]


event_type start_date end_date  \
1       Subscription       1921      NaN   
4       Subscription       1922      NaN   
6       Subscription       1923     1923   
7       Subscription       1923      NaN   
9       Subscription       1923      NaN   
...              ...        ...      ...   
35512  Reimbursement        NaN      NaN   
35517  Reimbursement        NaN      NaN   
35518  Reimbursement        NaN      NaN   
35520  Reimbursement        NaN      NaN   
35522  Reimbursement        NaN      NaN   

                                             member_uris        member_names  \
1      https://shakespeareandco.princeton.edu/members...         Mme Garreta   
4      https://shakespeareandco.princeton.edu/members...         Mr. Lincoln   
6      https://shakespeareandco.princeton.edu/members...      S. Q. Millward   
7      https://shakespeareandco.princeton.edu/members...       Mr. Foulquier   
9      https://shakespeareandco.princeton.edu/members...      Mrs. Hefferson   
...                                                  ...                 ...   
35512  https://shakespeareandco.princeton.edu/members...  Mrs. N. F. Connont   
35517  https://shakespeareandco.princeton.edu/members...       Austin Clarke   
35518  https://shakespeareandco.princeton.edu/members...       Henri Gutmann   
35520  https://shakespeareandco.princeton.edu/members...         Mr. Baldwin   
35522  https://shakespeareandco.princeton.edu/members...        M. A. Davies   

         member_sort_names  subscription_price_paid  subscription_deposit  \
1             Garreta, Mme                      NaN                   NaN   
4             Lincoln, Mr.                      NaN                   7.0   
6          Millward, S. Q.                      NaN                   NaN   
7           Foulquier, Mr.                      NaN                   NaN   
9          Hefferson, Mrs.                      NaN                   NaN   
...                    ...                      ...                   ...   
35512  Connont, Mrs. N. F.                      NaN                   NaN   
35517       Clarke, Austin                      NaN                   NaN   
35518       Gutmann, Henri                      NaN                   NaN   
35520         Baldwin, Mr.                      NaN                   NaN   
35522        Davies, M. A.                      NaN                   NaN   

      subscription_duration  subscription_duration_days  subscription_volumes  \
1                       NaN                         NaN                   NaN   
4                       NaN                         NaN                   NaN   
6                       NaN                         NaN                   NaN   
7                       NaN                         NaN                   NaN   
9                       NaN                         NaN                   NaN   
...                     ...                         ...                   ...   
35512                   NaN                         NaN                   NaN   
35517                   NaN                         NaN                   NaN   
35518                   NaN                         NaN                   NaN   
35520                   NaN                         NaN                   NaN   
35522                   NaN                         NaN                   NaN   

      subscription_category subscription_purchase_date  reimbursement_refund  \
1                       NaN                       1921                   NaN   
4                       NaN                       1922                   NaN   
6                       NaN                       1923                   NaN   
7                       NaN                       1923                   NaN   
9                       NaN                       1923                   NaN   
...                     ...                        ...                   ...   
35512                   NaN                        NaN        

In [15]:
test['start_datetime'] = pd.to_datetime(test.start_date, format='%Y-%m-%d', errors='coerce')
test['end_datetime'] = pd.to_datetime(test.end_date, format='%Y-%m-%d', errors='coerce')

In [26]:
alt.Chart(test[test.event_type == 'Subscription']).mark_bar().encode(
    x='year(start_datetime):T',
    y='count():Q',
)

alt.Chart(...)

In [21]:
test.to_csv('subscriptions_data.csv', index=False)

In [28]:
test.groupby(['event_type', 'year']).size().reset_index(name='counts').to_csv('subscriptions_data.csv', index=False)

In [27]:
test['year'] = test.start_datetime.dt.year

In [31]:
test.groupby(['event_type', 'year']).size()

event_type     year  
Reimbursement  1920.0     19
               1921.0     47
               1922.0     66
               1923.0    102
               1924.0    229
                        ... 
Supplement     1936.0      5
               1938.0      3
               1939.0      7
               1940.0      5
               1941.0      5
Length: 105, dtype: int64